In [1]:
from visualization_fct import *
# from bokeh.plotting import output_file, show, save
from bokeh.io import output_notebook
output_notebook()
from bokeh.plotting import show  # output_file, save

from bokeh.resources import CDN
from bokeh.embed import file_html


from pomegranate import GeneralMixtureModel
from pomegranate import MultivariateGaussianDistribution

import matplotlib.pyplot as plt  # , mpld3

data = pd.read_csv("../asm_data/asm_data_for_ml.txt", sep='\t')
del data['MJD']
# del data['error']
# del data['errorA']
# del data['errorB']
# del data['errorC']
data['rateCA'] = data.rateC / data.rateA
data_thr = mask(data, 'orbit')  # rm too large values except for 'orbit'

w = np.concatenate([np.array(data_thr[name]).reshape(-1, 1)
                    for name in ['error', 'errorA', 'errorB', 'errorC']],
                   axis=1)

# XXX add the error for the ratio:
w = np.concatenate([w, (data_thr['errorC'] / data_thr['rateA']).reshape(-1, 1)], axis=1)

del data_thr['error']
del data_thr['errorA']
del data_thr['errorB']
del data_thr['errorC']


np.random.seed(0)

X = np.c_[data_thr.orbit, data_thr.rate, data_thr.rateA, data_thr.rateB,
          data_thr.rateC, data_thr.rateCA]

from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
X = scaler.fit_transform(X)
w = w / np.sqrt(scaler.var_[1:])

Loading BokehJS ...

In [2]:
w = np.exp(-np.exp(3 * w.mean(axis=1)))
gmm = GeneralMixtureModel(MultivariateGaussianDistribution, n_components=3)
gmm.fit(X, weights=w)
preds = gmm.predict(X)
probs = gmm.predict_proba(X)

data_thr['preds'] = pd.Series(preds).astype("category")

color_key = ["red", "blue", "yellow", "grey", "black", "purple", "pink",
             "brown", "green", "orange"]  # Spectral9
color_key = color_key[:len(set(preds))+1]

covs = np.array([np.array(gmm.distributions[m].parameters[1])
                 for m in range(len(gmm.distributions))])
means = np.array([np.array(gmm.distributions[m].parameters[0])
                  for m in range(len(gmm.distributions))])

#covs = np.array([scaler.inverse_transform(scaler.inverse_transform(covs[j].T).T) for j in range(covs.shape[0])])
covs = np.array([np.dot(np.diag(np.sqrt(scaler.var_)), np.dot(covs[j], np.diag(np.sqrt(scaler.var_)))) for j in range(covs.shape[0])])
means = np.array([scaler.inverse_transform(means[j].reshape(1,-1)).T for j in range(means.shape[0])])

In [5]:
# single plot rateCA vs rate with predicted classes and ellipses:
x = 5
y = 1
covs_xy = [covs[j][[x, y]][:, [x, y]] for j in range(len(covs))]
means_xy = [means[j][[x, y]] for j in range(len(covs))]

single_plot = bokeh_datashader_plot(data_thr, covs=covs_xy, means=means_xy,
                                    x_name='rateCA',
                                    y_name='rate',
                                    plot_width=900, plot_height=300,
                                    
                                    pixel_width=3000, pixel_height=1000,
                                    spread=True, color_key=color_key)
show(single_plot)

> /home/nicolas/Documents/NYU-black_holes/code/visualization_fct.py(148)bokeh_datashader_plot()
-> t = np.linspace(0, 2 * np.pi, 10000)
(Pdb) c
> /home/nicolas/Documents/NYU-black_holes/code/visualization_fct.py(147)bokeh_datashader_plot()
-> pdb.set_trace()
(Pdb) c
> /home/nicolas/Documents/NYU-black_holes/code/visualization_fct.py(148)bokeh_datashader_plot()
-> t = np.linspace(0, 2 * np.pi, 10000)
(Pdb) c
